<html>
<head>
<style>
    body {
        font-family: 'Arial', sans-serif;
        margin-left: 40px;
        background: #ECE9E6;  /* Color de fondo general */
        background: -webkit-linear-gradient(to right, #FFFFFF, #ECE9E6);  /* Degradado para Chrome */
        background: linear-gradient(to right, #FFFFFF, #ECE9E6);  /* Degradado estándar */
    }
    .header {
        color: #2E86C1; /* Azul oscuro */
        padding-bottom: 10px;
        font-size: 32px;
        font-weight: bold;
        border-bottom: 3px solid #2E86C1; /* Borde con el mismo color para consistencia */
    }
    .subheader {
        color: #3498DB; /* Azul un poco más claro */
        padding-top: 5px;
        font-size: 24px;
    }
    .description {
        color: #5DADE2; /* Azul aún más claro para el cuerpo de texto */
        padding: 20px 0;
        font-size: 16px;
        text-align: left;
    }
    .footer {
        color: #AED6F1; /* Azul muy claro para la fecha */
        font-size: 14px;
        padding-top: 30px;
    }
</style>
</head>
<body>

<div class="header">
    Predictor del total de ingresos hospitalarios por enfermedades respiratorias en algunas zonas de la Ciudad de México
</div>

<div class="subheader">
    ANÁLISIS EXPLORATORIO DEL SET DE DATOS
</div>

<div class="description">
    <br><br>
    En este notebook exploraremos el set de datos con el cual podemos realizar una predicción de los futuros ingresos hospitalarios por enfermedades respiratorias en algunas zonas de la Ciudad de México, con el fin de familiarizarnos con los datos que darán forma al modelo de Aprendizaje Profundo, evaluar su 'calidad', la cantidad de información reelevante que aporta y elegir las variables que más utilizaremos para el entrenamiento del modelo que efectuará la predicción de la variable de estudio
</div>

<div class="footer">
    Fecha: <strong>27 de marzo de 2024</strong>
</div>

</body>
</html>


### Este análisis exploratorio de datos comprenderá 4 puntos:

1. Análisis exploratorio espacial
2. Análisis exploratorio de la continuidad de la Serie de Tiempo
3. Análisis exploratorio de las variables de estudio
4. Análisis Viusal de la Tendencia y el Nivel de la Serie de Tiempo

In [29]:
# Bibliotecas utilizadas en el análisis exploratorio
import pandas as pd
import numpy as np
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
import matplotlib.pyplot as plt
import folium
import pandas as pd
from shapely.geometry import MultiPoint
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
import plotly.express as px

## _Funciones_

In [30]:
def crear_sub_dataset(dataframe, columnas):
    """
    Crea un sub-dataset a partir de las columnas especificadas de un DataFrame.

    Parámetros:
    - dataframe: DataFrame de pandas del cual crear el sub-dataset.
    - columnas: Lista de strings con los nombres de las columnas a incluir en el sub-dataset.

    Retorna:
    - Un nuevo DataFrame que contiene solo las columnas especificadas.
    """
    sub_dataset = dataframe[columnas].copy()
    return sub_dataset

In [31]:
def agregar_numero_delegacion(df):
    df['numero_delegacion'] = df['clave_res'].apply(lambda x: int(x[2:5]))
    return df

In [32]:
def contar_registros_por_año_y_cluster(df):
    df['Año'] = df['FECHA'].dt.year
    conteo = df.groupby(['Año', 'numero_delegacion']).size().reset_index(name='Conteo')
    return conteo

### Carga del set de datos

In [33]:
df_enfermedades = pd.read_csv('2009_2022_Enfermedades_Respiratorias_COVID.csv', dtype={'clave_res': str})
df_enfermedades['FECHA'] = pd.to_datetime(df_enfermedades['FECHA'], format='%d/%m/%Y')

----------------------------------------------------------------------------

## _1. Análisis exploratorio espacial_
En esta sección, veremos como estan distribuidos las muestras de los datos a lo largo del terriotorio de la Ciudad de México, para analizar si pueden existir ciertos sesgos de localidad (por ejemplo que haya más muestras en cierta área que en otra) y esto ocasione una tendencia en la predicción que deseamos hacer


### _1.1 Clasificación de los registros por Alcaldía_
Añadimos una nueva columna al set de datos que corresponde al número de alcaldía a la que se relaciona cada uno de los registros de incidencias.
_POR EJEMPLO:_ A un registro que se relaciona con la localidad '090090336' se le asigna en una nueva columna llamada numero_delegacion el valor de 9.

In [34]:
df_enfermedades = agregar_numero_delegacion(df_enfermedades)
df_enfermedades = crear_sub_dataset(df_enfermedades, ["numero_delegacion", "LAT_DECIMAL", "LON_DECIMAL", "FECHA", "Total_Ingresos_Respiratorios_COVID", "Temperatura Promedio","Humedad relativa Promedio","PM25 Promedio","PM10 Promedio","O3 Promedio","SO2 Promedio", "CO Promedio","NO2 Promedio","NOX Promedio","NO Promedio"])
print(df_enfermedades.head())

   numero_delegacion  LAT_DECIMAL  LON_DECIMAL      FECHA  \
0                  8    19.304898   -99.241515 2009-01-01   
1                 14    19.371992   -99.157853 2009-01-01   
2                  4    19.357350   -99.299792 2009-01-01   
3                  9    19.191988   -99.089954 2009-01-01   
4                  5    19.482945   -99.113471 2009-01-01   

   Total_Ingresos_Respiratorios_COVID  Temperatura Promedio  \
0                                  12              13.50805   
1                                   9              13.85766   
2                                   8              13.38054   
3                                   1              13.65075   
4                                  94              14.18049   

   Humedad relativa Promedio  PM25 Promedio  PM10 Promedio  O3 Promedio  \
0                   48.25448       32.38168       54.07328     25.75485   
1                   48.46696       31.28841       61.75105     22.11455   
2                   48.72771 

### _1.2 Spatial data visualization_ 
Proponemos visualizar los puntos de mayor índice de ingresos hospitalarios para observar su distribución espacial en un mapa, y con ello determinar si contamos con una muestra representativa de los datos, que garantizarían una predicción de alta exactitud

In [35]:
lat_center = df_enfermedades['LAT_DECIMAL'].mean()
lon_center = df_enfermedades['LON_DECIMAL'].mean()

m = folium.Map(location=[lat_center, lon_center], zoom_start=11)

cluster_colors = {
    2: 'red',
    3: 'blue',
    4: 'green',
    5: 'purple',
    6: 'orange',
    7: 'pink',
    8: 'yellow',
    9: 'cyan',
    10: 'magenta',
    11: 'brown',
    12: 'lime',
    13: 'teal',
    14: 'olive',
    15: 'navy',
    16: 'maroon',
    17: 'silver',

}

for cluster in df_enfermedades['numero_delegacion'].unique():
    points = df_enfermedades[df_enfermedades['numero_delegacion'] == cluster][['LAT_DECIMAL', 'LON_DECIMAL']].values

    for point in points:
        folium.CircleMarker(location=[point[0], point[1]],
                            radius=5,
                            color=cluster_colors[cluster],
                            fill=True,
                            fill_color=cluster_colors[cluster],
                            fill_opacity=0.6).add_to(m)

    multipoint = MultiPoint(points)
    
area_names = {
    2: 'Azcapotzalco',
    3: 'Coyoacán',
    4: 'Cuajimalpa de Morelos',
    5: 'Gustavo A. Madero',
    6: 'Iztacalco',
    7: 'Iztapalapa',
    8: 'La Magdalena Contreras',
    9: 'Milpa Alta',
    10: 'Álvaro Obregón',
    11: 'Tláhuac',
    12: 'Tlalpan',
    13: 'Xochimilco',
    14: 'Benito Juárez',
    15: 'Cuauhtémoc',
    16: 'Miguel Hidalgo',
    17: 'Venustiano Carranza',
}

legend_html = '''
<div style="position: fixed; 
    bottom: 150px; left: 50px; width: 200px; height: 240px; 
    background-color: white; border:2px solid grey; z-index:9999; font-size:14px;
    ">&nbsp; Leyenda <br>
    &nbsp; Cluster y Área <br>
    {}
</div>
'''

legend_entries = ''
for cluster, color in cluster_colors.items():
    name = area_names.get(cluster, 'N/A')
    legend_entries += f'&nbsp; <i class="fa fa-circle fa-1x" style="color:{color}"></i> {name} <br>'

legend_html = legend_html.format(legend_entries)

m.get_root().html.add_child(folium.Element(legend_html))

In [36]:
# Visualización del mapa
m

### _1.3 Observaciones generales_
- El set de datos se encuentra des-balanceado espacialmente _(en Tlalpan hay más localidades registradas que en Iztacalco, por ejemplo)_.
- Hay alcaldías altamente pobladas como Iztapalapa que solamente cuentan con una localidad registrada.


### _1.4 Conclusiones preliminares_
Las observacions generales nos pueden hacer concluir lo siguiente: 

* Dado que el set de datos cuenta con diferentes _puntos específicos_ de la Ciudad de México donde se registra un mayor índice de ingresos hospitalarios, es probable que la cantidad de muestras no alcance para realizar una predicción _global a nivel Ciudad de México_ con precisión adecuada. Por lo cual, se propone atacar el problema con unfoque _local_

* Para algunas zonas la predicción puede no ser representativo a lo que esté sucediendo realmente, dado el desbalance espacial del set de datos.

* Dado que hay alcaldías que solo cuentan con una localidad como objeto de estudio, podemos proponer que el estudio _local_ se realice por _zonas dentro de la Ciudad de México_ (en lugar de hacerlo por alcaldías). **VER NOTEBOOK: analisisExploratorio02.ipynb**

----------------------------------------------------------------------------
## _2. Análisis exploratorio de la continuidad de la Serie de Tiempo_
En esta sección se pretende ver la continuidad de la serie de tiempo con la que contamos en el set de datos, es decir o existen registros faltantes, cuántos son los registros faltantes (si es que los hay) y cómo estos factores pueden afectar la predicción de los futuros datos de ingresos hospitalarios en algunas zonas de la Ciudad de México.

### _2.1 Agrupación de los registros por delegación_

Existen fechas en las que hay más de una localidad por delegación, entonces agrupamos todos los registros que pertenezcan a una misma delegación y a una misma fecha en uno sólo, con las siguientes puntualizaciones:

- El número de ingresos respiratorios se _suma_.
- El valor de las variables que evalúan la calidad del aire se _promedia._

In [37]:
df_enfermedades_c = df_enfermedades.groupby(['FECHA', 'numero_delegacion']).agg({
        'Total_Ingresos_Respiratorios_COVID': 'sum',
        'Temperatura Promedio': 'mean',
        'Humedad relativa Promedio': 'mean',
        'PM25 Promedio': 'mean',
        'PM10 Promedio': 'mean',
        'O3 Promedio': 'mean',
        'SO2 Promedio': 'mean',
        'CO Promedio': 'mean', 
        'NO2 Promedio': 'mean',
        'NOX Promedio': 'mean',
        'NO Promedio': 'mean'
    }).reset_index()

print(df_enfermedades_c.head())

       FECHA  numero_delegacion  Total_Ingresos_Respiratorios_COVID  \
0 2009-01-01                  2                                  45   
1 2009-01-01                  3                                  30   
2 2009-01-01                  4                                   8   
3 2009-01-01                  5                                  94   
4 2009-01-01                  6                                  25   

   Temperatura Promedio  Humedad relativa Promedio  PM25 Promedio  \
0              14.04355                   48.51882       34.94763   
1              13.67971                   48.38166       30.79451   
2              13.38054                   48.72771       32.95124   
3              14.18049                   47.47852       33.06992   
4              14.15907                   48.46493       32.16271   

   PM10 Promedio  O3 Promedio  SO2 Promedio  CO Promedio  NO2 Promedio  \
0       73.56560     22.90932       8.50679      1.47031      41.44705   
1       59

### _2.2 Detección de registros faltantes_

Dentro de todas las fechas existentes en el set de datos, observamos si hay alguna alcaldía que no cuente con datos para una fecha específíca

In [38]:
for fecha in df_enfermedades_c['FECHA'].unique():
    registros_fecha = df_enfermedades_c[df_enfermedades_c['FECHA'] == fecha]

    delegaciones_presentes = set(registros_fecha['numero_delegacion'])
    
    # Verificar si falta algún número del 2 al 17
    for i in range(2, 18):
        if i not in delegaciones_presentes:
            print(f"Falta la delegación {i} en la fecha {fecha}")

Falta la delegación 4 en la fecha 2011-08-01 00:00:00
Falta la delegación 4 en la fecha 2013-02-01 00:00:00
Falta la delegación 4 en la fecha 2014-03-01 00:00:00
Falta la delegación 4 en la fecha 2015-12-01 00:00:00


### _2.3 Observaciones generales_
- Para la delegación marcada con el número 4 _(Cuajimalpa de Morelos)_ existen 4 registros faltantes para que su serie de tiempo se encuentre completamente bien definida, tales registros corresponden a los meses de agosto/2011, febrero/2013, marzo/2014 y diciembre/2015.


### _2.4 Conclusiones preliminares_
Las observacions generales nos pueden hacer concluir lo siguiente: 

* La serie de tiempo en cuanto a su continuidad se encuentra bien definida, pues solo existen 4 registros faltantes para todo el periodo de enero de 2009 a diciembre de 2022, los 4 correspondientes a la alcaldía de Cuajimalpa de Morelos
* Dichos registros faltantes, al no representar una cantidad considerable, pueden ser estimados con técnicas de _imputación de datos_

----------------------------------------------------------------------------
## _3. Análisis exploratorio de las variables de estudio_
En esta sección veremos la relación existente entre las variables propuestas de contaminación del aire y el total de ingresos respiratorios a lo largo del tiempo, esto con el fin de ver cuales son las variables atmosféricas que más contribuyen (o las que más peso tienen) en los ingresos hospitalarios respiratorios. Este es un paso vital, pues de la relación existente entre las variables mencionadas anteriormente. dependerá que exista o no una predicción adecuada de los datos futuros, pues si no existe una relación fuerte, seguramente esto significaría una baja eficiencia en el modelo predictivo comparado con los datos reales.

### _3.1 Elección de un caso de estudio_
Para ello, seleccionaremos como caso de estudio el de la alcaldía de código 003, es decir Coyoacán.

In [39]:
df_del03 = df_enfermedades_c[df_enfermedades_c['numero_delegacion'] == 3]
print(df_del03.head())

        FECHA  numero_delegacion  Total_Ingresos_Respiratorios_COVID  \
1  2009-01-01                  3                                  30   
17 2009-02-01                  3                                  28   
33 2009-03-01                  3                                  52   
49 2009-04-01                  3                                  29   
65 2009-05-01                  3                                  28   

    Temperatura Promedio  Humedad relativa Promedio  PM25 Promedio  \
1               13.67971                   48.38166       30.79451   
17              15.01695                   43.59485       28.51546   
33              16.90069                   36.43377       27.02844   
49              19.30621                   34.46198       28.78494   
65              18.87053                   47.50797       26.49763   

    PM10 Promedio  O3 Promedio  SO2 Promedio  CO Promedio  NO2 Promedio  \
1        59.09205     22.59123       8.12307      1.30810      40.22724

### _3.2 Cálculo de la correlación entre el Total_Ingresos_Respiratorios_COVID VS el conjunto de variables atmosféricas_

**_Explicación de la matriz de correlación:_**

La matriz de correlación es una herramienta estadística que se utiliza para evaluar la fuerza y la dirección de las relaciones lineales entre dos o más variables. En el contexto de la calidad del aire y las hospitalizaciones por enfermedades respiratorias, nos permite examinar cómo las diferentes variables ambientales (como los niveles de PM2.5, NO2, O3, etc.) se relacionan entre sí y con el número de hospitalizaciones.

Cada elemento de la matriz representa el coeficiente de correlación entre dos variables. Este coeficiente puede variar entre -1 y 1, donde:

- **1** indica una correlación positiva perfecta: a medida que una variable aumenta, la otra también lo hace.
- **-1** indica una correlación negativa perfecta: a medida que una variable aumenta, la otra disminuye.
- **0** indica ninguna correlación lineal: las variables no se mueven juntas en ninguna dirección lineal específica.

**_Interpretación de la Matriz de Correlación_**

Al interpretar la matriz de correlación, buscamos coeficientes que sean significativamente distintos de 0, lo que indicaría una relación lineal. Un coeficiente cercano a 1 o -1 sugiere una fuerte relación lineal, mientras que valores cercanos a 0 sugieren una relación lineal débil o inexistente.

Es importante tener en cuenta que la correlación no implica causalidad. Incluso si dos variables están fuertemente correlacionadas, no podemos asumir de inmediato que una causa los cambios en la otra sin un análisis más profundo.

In [40]:
variables = ["Temperatura Promedio", 
        "Humedad relativa Promedio", 
        'Temperatura Promedio',
        'Humedad relativa Promedio',
        'PM25 Promedio',
        'PM10 Promedio',
        'O3 Promedio',
        'SO2 Promedio',
        'CO Promedio',
        'NO2 Promedio',
        'NOX Promedio',
        'NO Promedio']

for var in variables:
    print(f"Correlación con {var}")
    corr_matrix = df_del03[["Total_Ingresos_Respiratorios_COVID", var]].corr()
    print(f"Matriz de Correlación: Total_Ingresos_Respiratorios_COVID vs {var}")
    print(corr_matrix)
    print(" \n\n\n")

Correlación con Temperatura Promedio
Matriz de Correlación: Total_Ingresos_Respiratorios_COVID vs Temperatura Promedio
                                    Total_Ingresos_Respiratorios_COVID  \
Total_Ingresos_Respiratorios_COVID                            1.000000   
Temperatura Promedio                                          0.034797   

                                    Temperatura Promedio  
Total_Ingresos_Respiratorios_COVID              0.034797  
Temperatura Promedio                            1.000000  
 



Correlación con Humedad relativa Promedio
Matriz de Correlación: Total_Ingresos_Respiratorios_COVID vs Humedad relativa Promedio
                                    Total_Ingresos_Respiratorios_COVID  \
Total_Ingresos_Respiratorios_COVID                            1.000000   
Humedad relativa Promedio                                    -0.061047   

                                    Humedad relativa Promedio  
Total_Ingresos_Respiratorios_COVID                  -0.06104

### _3.3 Observaciones generales_
- Se realizaron 12 matrices de correación entre las variables atmosféricas (listadas en el código) vs el total de casos que requirieron hospitalización en la delegación.
- Se observa que 2/12 correlaciones son positivas (cuando una variable aumenta, la otra también lo hace); siendo la mayor de ellas de **0.050082** presente en el **O3 Promedio**. Lo que indica que hay muy baja relación lineal entre las variables atmosféricas y el total casos de hospitalización presentes en el set de datos.
- Se observa que 10/12 correlaciones son negativas (cuando una variable aumenta, la otra disminuye); siendo la menor de ellas de **-0.397539** presente en el **CO Promedio** Lo que indica que hay muy baja relación lineal entre las variables atmosféricas y el total casos de hospitalización presentes en el set de datos


### _3.4 Conclusiones preliminares_
Las observacions generales nos pueden hacer concluir lo siguiente: 

* No hay indicios de que exista relación lineal fuerte entre las variables que evalúan la calidad del aire y el total de ingresos hospitalarios por enfermedades respiratorias
* Podríamos seleccionar aquellas variables que presentan una correlación lineal más fuerte
* Para la selección de las demás variables que tendrán participación en el modelo, podemos proponerlas empíricamente

----------------------------------------------------------------------------
## _4. Análisis Viusal de la Tendencia y el Nivel de la Serie de Tiempo_
En esta sección exploraremos a nivel visual cómo los datos contribuyen a darle forma al nivel y a la tendencia de la Serie de Tiempo que tenemos actualmente

### _4.1 Inspección visual de la serie de tiempo desde 2009 hasta 2022_ 
Seguiremos trabajando con el caso de estudio de la alcaldía Cuajimalpa de Morelos

In [41]:
df_del03['Promedio_Movil'] = df_del03['Total_Ingresos_Respiratorios_COVID'].rolling(window=5, min_periods=1).mean()

fig = px.line(df_del03, x='FECHA', y='Total_Ingresos_Respiratorios_COVID', title='Contagios de COVID con Respecto al Tiempo')

fig.add_scatter(x=df_del03['FECHA'], y=df_del03['Promedio_Movil'], mode='lines', name='Nivel (Promedio Móvil)')

fig.show()

/tmp/ipykernel_5419/2568876704.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/usr/lib/python3/dist-packages/_plotly_utils/basevalidators.py:107: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result

/usr/lib/python3/dist-packages/_plotly_utils/basevalidators.py:107: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



### _4.2 Inspección visual de la serie de tiempo desde 2009 hasta 2020_

In [42]:
fig = px.line(df_del03[df_del03['FECHA'] < '2020-01-01'], x='FECHA', y='Total_Ingresos_Respiratorios_COVID', title='Contagios de COVID con Respecto al Tiempo')
fig.show()

/usr/lib/python3/dist-packages/_plotly_utils/basevalidators.py:107: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [43]:
print(f"Promedio de ingresos hospitalarios entre 2009 y 2020: {df_del03[(df_del03['FECHA'] >= '2009-01-01') & (df_del03['FECHA'] <= '2019-12-31')]['Total_Ingresos_Respiratorios_COVID'].mean()}")
print(f"Promedio de ingresos hospitalarios entre 2020 y 2022: {df_del03[(df_del03['FECHA'] >= '2020-01-01') & (df_del03['FECHA'] <= '2022-12-31')]['Total_Ingresos_Respiratorios_COVID'].mean()}")

Promedio de ingresos hospitalarios entre 2009 y 2020: 35.553030303030305
Promedio de ingresos hospitalarios entre 2020 y 2022: 10691.666666666666


### _4.3 Observaciones generales_
- En una serie de tiempo tenemos una progresión secuencial de datos, lo que implica que la salida de un sistema en un tiempo _t_ depende a su vez, de la salida que dicho sistema tuvo en un tiempo _t-1_.
- El conjunto de datos del que tenemos conocimiento tiene registros únicamente hasta el año 2022 (no hay datos de 2023).
- Todos los datos que tenemos registrados, referente a la alcaldía Cuajimalpa de Morelos, alcanzan un máximo de 70 casos de ingresos hospitalarios _en el periodo 2009 a 2020_
- En el periodo de 2009 a 2020 el promedio de casos que requirieron hospitalización es de 36
- En el periodo de 2020 a 2022 el promedio de casos que requirieron hospitalización es de 10692
- El nivel que tiene la Serie de Tiempo antes y después de la aparición del Virus SARS-COV2 es muy grande


### _4.4 Conclusiones preliminares_
Las observacions generales nos pueden hacer concluir lo siguiente: 

* Actualmente, disponemos de datos hasta el año 2022, incluyendo tanto las variables atmosféricas como los registros de enfermedades respiratorias. Nuestro objetivo es pronosticar los eventos para los años 2024 y 2025. Sin embargo, dado que la precisión de nuestras predicciones para un año dado depende directamente de la información disponible de años anteriores, es necesario primero estimar los datos para 2023. Así, la exactitud de nuestras proyecciones para 2024 se basa en las estimaciones realizadas para 2023, y lo mismo ocurre para las predicciones de 2025 respecto a 2024. Esto implica que cuanto más nos proyectemos hacia el futuro, es probable que enfrentemos una mayor incertidumbre y posibles imprecisiones en nuestras predicciones.

* El nivel de la serie de tiempo, tanto antes como después del surgimiento del Covid-19, es notoriamente alto debido a una variable desconocida y no registrada (la aparición de la pandemia) en nuestro conjunto de datos, la cual, además, resulta imposible de medir. Este incremento del nivel sugiere que nuestra serie de tiempo, que abarca desde 2009 hasta 2020, podría no ser la base más fiable para hacer proyecciones hacia 2023 y más allá.Dado que el nivel de la Serie de Tiempo, antes y después de la aparición del Covid 19 es muy alto, y el incremento de este nivel se debe a una variable de la que no tenemos registro en nuestro set de datos, y que de hecho no podríamos medir, es probable que la serie de tiempo que tenemos de 2009 al 2020, sea ineficiente para realizar predicciones para el año 2023, 2024 y 2025.

* Este escenario nos deja con solo dos años de datos post aparición del Covid (2020, 2021 y 2022), equivalentes a 36 muestras, que podrían considerarse relevantes para nuestras predicciones futuras. Esta limitación en la cantidad de datos pertinentes plantea un desafío significativo.

* Finalmente, la cantidad limitada de muestras juega un papel crucial en la precisión de nuestras predicciones futuras. Con solo 36 muestras significativas disponibles, la capacidad para realizar pronósticos precisos para los años siguientes se puede ver comprometida.

Predictor
    Input(Variables ambientales, variable_epidem(actual))
    Output(variable_epidem(actual+1))

Predictor
    Input(variable_epidem(actual)) -> 51
    Output(variable_epidem(actual+1)) -> 55